In [1]:
import numpy as np
import plotly.graph_objects
from ipywidgets import interactive_output, VBox, HBox, SelectionSlider


In [2]:
mydefault = plotly.graph_objects.layout.Template()
mydefault.layout.xaxis.showgrid = False
mydefault.layout.yaxis.showgrid = False
mydefault.layout.xaxis.showline = True
mydefault.layout.yaxis.showline = True
mydefault.layout.yaxis.linewidth = 2
mydefault.layout.xaxis.ticks = "outside"
mydefault.layout.yaxis.ticks = "outside"
mydefault.layout.hovermode = False
mydefault.layout.dragmode = "pan"
mydefault.layout.scene.hovermode = False
mydefault.layout.xaxis.showspikes = False
mydefault.layout.yaxis.showspikes = False
mydefault.layout.scene.xaxis.showspikes = False
mydefault.layout.scene.yaxis.showspikes = False
mydefault.layout.scene.zaxis.showspikes = False
plotly.io.templates["mydefault"] = mydefault
plotly.io.templates.default = "mydefault"


**Recall the concept of a *strange attractor***

In [3]:
state_vars = list(var("G, S, W"))
system = (
    G*(1 - G/3) - 2.5*G/(1 + G)*S, 
    2/3*2.5*G/(1 + G)*S - 0.4*S - 0.1*S/(1 + S)*W, 
    0.5*0.1*S/(1 + S)*W - 0.01*W, 
)
vectorfield(G, S, W) = system
delta_t = 0.1
t_range = srange(0, 10000, delta_t)
initial_state = (1, 1, 1)
attractor = desolve_odeint(vectorfield, initial_state, t_range, state_vars)[int(2000/delta_t):]

fig = plotly.graph_objects.Figure()
fig.layout.showlegend = False
fig.layout.scene.xaxis.title.text = "G (grass)"
fig.layout.scene.yaxis.title.text = "S (sheep)"
fig.layout.scene.zaxis.title.text = "W (wolves)"
fig.layout.scene.xaxis.range = (0,  3.2)
fig.layout.scene.yaxis.range = (0,  1.2)
fig.layout.scene.zaxis.range = (7.3, 11.0)
fig.layout.scene.aspectmode = "cube"
fig.add_scatter3d(x=attractor[:,0], y=attractor[:,1], z=attractor[:,2], 
                  mode="lines", line_color="purple", opacity=0.5)
fig.show()


# The discrete-time logistic model: 

$$ X_{t+1} = 4 X_t \cdot ( 1 - X_t ) $$


In [3]:
def logistic_interactive():
    r_values = [round(r, 2) for r in srange(0.5, 3.4, 0.1) + srange(3.45, 4.001, 0.01)]
    t_range = srange(10000)
    discard = 200
    tmax = 500

    fig = plotly.subplots.make_subplots(rows=int(1), cols=int(2))
    fig = plotly.graph_objects.FigureWidget(fig)
    fig.layout.showlegend = False
    fig.layout.margin.update(t=30, r=0)
    fig.layout.xaxis.title.text = "t"
    fig.layout.yaxis.title.text = "X"
    fig.layout.xaxis2.title.text = "Relative frequency"
    fig.layout.yaxis2.title.text = "X"
    fig.layout.xaxis.range = (0, 50)
    fig.layout.yaxis.range = (0, 1.05)
    fig.layout.xaxis2.range = (0, 1)
    fig.layout.yaxis2.range = (0, 1.05)
    fig.add_scatter(row=int(1), col=int(1), x=t_range[:tmax], marker_color="blue", line_color="gray")
    timeseries = fig.data[-1]
    fig.add_bar(row=int(1), col=int(2), orientation="h")
    bar_chart = fig.data[-1]

    X_min, X_max, X_bins = 0, 1, 50
    bin_width = (X_max - X_min) / (X_bins - 1)
    bin_edges = np.array(srange(X_min, X_max + bin_width/2, bin_width), dtype=float)
    bin_middles = (bin_edges[:-1] + bin_edges[1:]) / 2
    bar_chart.y = bin_middles

    def update(r, X0):
        X_next = fast_float(r*x*(1 - x), x)
        X = X0
        solution = np.zeros([len(t_range)], dtype=float)
        for t in t_range:
            solution[t] = X
            X = X_next(X)
        histogram = np.histogram(solution[discard:], bin_edges, density=True)[0]
        histogram /= histogram.max()
        with fig.batch_update():
            timeseries.y = solution[:tmax]
            bar_chart.x = histogram

    def show_lines(change):
        if connect.value:
            with fig.batch_update():
                timeseries.mode = "markers+lines"
                show_dist.value = False
        else:
            timeseries.mode = "markers"

    def show_histogram(change):
        with fig.batch_update():
            bar_chart.visible = show_dist.value
            fig.layout.xaxis2.visible = show_dist.value
            fig.layout.yaxis2.visible = show_dist.value

    X_values = [round(r, 2) for r in srange(0.01, 0.991, 0.01)]
    r = SelectionSlider(options=r_values, value=4, description="r", continuous_update=False)
    X0 = SelectionSlider(options=X_values, description="Initial X:", continuous_update=False)
    connect = checkbox(True, label="Connect the dots")
    show_dist = checkbox(False, label="Show distribution")
    connect.observe(show_lines, "value")
    show_dist.observe(show_histogram, "value")
    show_lines(None)
    show_histogram(None)
    output = interactive_output(update, dict(r=r, X0=X0))
    display(HBox((r, X0, connect, show_dist)), fig, output)
    return fig


In [4]:
logistic_widget = logistic_interactive()


FigureWidget({
    'data': [{'line': {'color': 'gray'},
              'marker': {'color': 'blue'},
           …

Output()

# The discrete-time logistic model: 

$$ X_{t+1} = r X_t \cdot ( 1 - X_t ) $$

We have been only considering the case where $r = 4$. But what if we vary $r$? 
